In [6]:
import numpy as np
import math
import random
class Node:
    def __init__(self,numtheta):
        self.theta=[0.0]*numtheta
        self.downstream=None
        self.upstream=None
        self.output=None
        self.deljthetabydelthetaunit = [0.0]*numtheta
        self.deljthetabydelnet = None
def loadtheta(network,theta ):
    for i in range(len(network)):
        for j in range(len(network[i])):
            for k in range(len(network[i][j].theta)):
                network[i][j].theta[k] = theta[i][j][k]
    return network
def sigmoid(x):
    return (1.0/(1.0+math.exp(-x)))
def forwardpass(features, network):
    for i in range(len(network)):
        for j in range(len(network[i])):
            tempnode = network[i][j]
            temp=0.0
            if(i==0):
                #parse from input
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * features[k]
                
            else:
                #parse from last layer
                prevlayer = network[i-1]
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * prevlayer[k].output
            tempnode.output = sigmoid(temp)
    lastlayer = network[len(network)-1]
    templist=[]
    for i in range(len(lastlayer)):
        templist.append(lastlayer[i].output)
    return templist
def findcost(output, correctoutput):
    temp = 0.0
    for i in range(len(output)):
        temp += 0.5 * ((output[i]-correctoutput[i])**2)
    return temp
def findtotalcostarr(inparr,outarr,network):
    costarr=[]
    for i in range(len(inparr)):
        tempforwardpass= forwardpass(inparr[i],network)
        print("tempforwardpass is")
        print(tempforwardpass)
        tempcost = findcost(tempforwardpass,outarr[i])
        costarr.append(tempcost)
    avgcost=0.0
    for i in range(len(costarr)):
        avgcost += costarr[i]
    avgcost = avgcost/(len(costarr))
    return costarr, avgcost
def printdeljtheta(network):
    print("deljtheta is")
    templist=[]
    for i in range(len(network)):
        templist.append([])
        for j in range(len(network[i])):
            templist[i].append([])
            for k in range(len(network[i][j].theta)):
                templist[i][j].append(network[i][j].deljthetabydelthetaunit[k])
    print(templist)
    return
def neuralnet(inparr, outarr, hiddeninfo,learningrate, epochsize,costthres, sampletheta):
    numtrain = len(inparr)
    diminput= len(inparr[0])
    dimoutput = len(outarr[0])
    network=[]
    for i in range(len(hiddeninfo)):
        network.append([])
    network.append([])
    for i in range(len(hiddeninfo)):
        #i is layer iterator
        for j in range(hiddeninfo[i]):
            #j is sublayer num unit iterator
            if(i==0):
                tempnode = Node(diminput+1)
                network[i].append(tempnode)
            else:
                tempnode = Node(hiddeninfo[i-1]+1)
                network[i].append(tempnode)
            
    #add output layer
    for i in range(dimoutput):
        tempnode = Node(hiddeninfo[len(hiddeninfo)-1] + 1)
        network[len(network)-1].append(tempnode)
    #load theta for testing
#     network = loadtheta(network, sampletheta)
    #necessary forwardpass
#     tempforwardpass = forwardpass(inparr[0],network)
#     print(tempforwardpass)
#     #lets see cost
#     print("cost = "+str(findcost(tempforwardpass,outarr[0])))
    
    #time for backprop
    deljthetabydelthetamat=[]
    for i in range(len(network)):
        deljthetabydelthetamat.append([])
        for j in range(len(network[i])):
            deljthetabydelthetamat[i].append([])
            for k in range(len(network[i][j].theta)):
                deljthetabydelthetamat[i][j].append(0.0)
    print("simulated deljtheata")
    print(deljthetabydelthetamat)
    print("real deljtheta")
    printdeljtheta(network)
    subepochiter=0
    epochcount=0
    numwholedatapass=0
    numiter=0
    costarr,oldavgcost = findtotalcostarr(inparr,outarr,network)
    shufflehelper = []
    for i in range(len(inparr)):
    	shufflehelper.append(i)
    while(0==0):
        numiter+=1
        print("numiter is")
        print(numiter)
        print("numwholedata pass is")
        print(numwholedatapass)
        ioindex = epochsize*epochcount+subepochiter
        print("ioindex is "+str(ioindex))
        tempforwardpass = forwardpass(inparr[shufflehelper[ioindex]],network)
        for i in range(len(network)-1,-1,-1):
            #lets calculate deljtheta by del netj
            for j in range(len(network[i])):
                tempnode = network[i][j]
                if(i==len(network)-1):
                    tempnode.deljthetabydelnet = -1.0*(outarr[shufflehelper[ioindex]][j]-tempnode.output)*(tempnode.output)*(1.0-tempnode.output)
                else:
                    temp=0.0
                    nextlayer = network[i+1]
                    for k in range(len(nextlayer)):
                        temp += nextlayer[k].deljthetabydelnet * nextlayer[k].theta[j]
                    tempnode.deljthetabydelnet = (tempnode.output) * (1.0- tempnode.output) * temp
                if(i==0):
                    #ok is input
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * inparr[shufflehelper[ioindex]][k]
                else:
                    prevlayer = network[i-1]
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * prevlayer[k].output
        subepochiter+=1
        for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        deljthetabydelthetamat[i][j][k] += network[i][j].deljthetabydelthetaunit[k]
        print("simulated deljtheata")
        print(deljthetabydelthetamat)
        print("real deljtheta")
        printdeljtheta(network)
        if(subepochiter==epochsize):
            print("epoch over")
            for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        network[i][j].theta[k] = network[i][j].theta[k] - learningrate * deljthetabydelthetamat[i][j][k]/(1.0*epochsize)
                        deljthetabydelthetamat[i][j][k]=0.0
            #set deljthetabydel zero
            
            costarr, newavgcost=findtotalcostarr(inparr,outarr,network)
            print("cost is")
            print(newavgcost)
            if(newavgcost<costthres):
                print("cost is lower")
                break
            elif(numwholedatapass>=20000):
                break
            else:
                oldavgcost=newavgcost
                subepochiter=0
                epochcount+=1
                if(len(inparr)==epochcount*epochsize):
                    numwholedatapass+=1
                    epochcount=0
                    random.shuffle(shufflehelper)
        
            
            
            
#         tempforwardpass = forwardpass(inparr[0],network)
#         print(tempforwardpass)
#         #lets see cost
#         print("cost = "+str(findcost(tempforwardpass,outarr[0])))        
    
    return network
# sampleinparr = [[0.05, 0.10]]
sampleinparr = [[0.0, 1.0],[1.0,0.0],[0.0,0.0],[1.0,1.0]]

# sampleoutput = [[0.01, 0.99]]
sampleoutput = [[0.99],[0.99],[0.01],[0.99]]
samplehiddeninfo = [1]
samplelearningrate=1.0
sampletheta = [[[.15,.20,.35],[.25,.30,.35]],[[.40,.45,.60],[.50,.55,.60]]]

samplenetwork = neuralnet(sampleinparr,sampleoutput,samplehiddeninfo,samplelearningrate,1, pow(10,-4),sampletheta)
print(samplenetwork)
            
                
    
    

simulated deljtheata
[[[0.0, 0.0, 0.0]], [[0.0, 0.0]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0]], [[0.0, 0.0]]]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
numiter is
1
numwholedata pass is
0
ioindex is 0
simulated deljtheata
[[[0.0, 0.0, 0.0]], [[-0.06125, -0.1225]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0]], [[-0.06125, -0.1225]]]
epoch over
tempforwardpass is
[0.538206625748814]
tempforwardpass is
[0.538206625748814]
tempforwardpass is
[0.538206625748814]
tempforwardpass is
[0.538206625748814]
cost is
0.11141924981709554
numiter is
2
numwholedata pass is
0
ioindex is 1
simulated deljtheata
[[[-0.0017194228606388733, 0.0, -0.0017194228606388733]], [[-0.056144419939228515, -0.11228883987845703]]]
real deljtheta
deljtheta is
[[[-0.0017194228606388733, -0.0, -0.0017194228606388733]], [[-0.056144419939228515, -0.11228883987845703]]]
epoch over
tempforwardpass is
[0.5728617084536598]
tempforwardpass is
[0.5728740561549244]


78
numwholedata pass is
19
ioindex is 1
simulated deljtheata
[[[-0.005451649588894102, -0.005451649588894102, -0.005451649588894102]], [[-0.0299236264835461, -0.05092045293133436]]]
real deljtheta
deljtheta is
[[[-0.005451649588894102, -0.005451649588894102, -0.005451649588894102]], [[-0.0299236264835461, -0.05092045293133436]]]
epoch over
tempforwardpass is
[0.7405297728655018]
tempforwardpass is
[0.7404894742210195]
tempforwardpass is
[0.7362652266280205]
tempforwardpass is
[0.7446386816843114]
cost is
0.08901928157946301
numiter is
79
numwholedata pass is
19
ioindex is 2
simulated deljtheata
[[[0.0, -0.005605346100179745, -0.005605346100179745]], [[-0.026174464932015702, -0.047934563657139384]]]
real deljtheta
deljtheta is
[[[-0.0, -0.005605346100179745, -0.005605346100179745]], [[-0.026174464932015702, -0.047934563657139384]]]
epoch over
tempforwardpass is
[0.7525639574959712]
tempforwardpass is
[0.7523939938754858]
tempforwardpass is
[0.7480701926428603]
tempforwardpass is
[0.7567

epoch over
tempforwardpass is
[0.772305892596854]
tempforwardpass is
[0.7724833885634433]
tempforwardpass is
[0.7605113001010687]
tempforwardpass is
[0.7831243344441462]
cost is
0.08759611915343353
numiter is
150
numwholedata pass is
37
ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.02348676703387004]], [[0.06706324064665471, 0.1366935219520525]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.02348676703387004]], [[0.06706324064665471, 0.1366935219520525]]]
epoch over
tempforwardpass is
[0.7391997733082339]
tempforwardpass is
[0.7393760879965374]
tempforwardpass is
[0.7275541196968792]
tempforwardpass is
[0.7500055660962409]
cost is
0.0872742927469137
numiter is
151
numwholedata pass is
37
ioindex is 2
simulated deljtheata
[[[0.0, -0.007304271441700154, -0.007304271441700154]], [[-0.028079025579569913, -0.048350137589506736]]]
real deljtheta
deljtheta is
[[[-0.0, -0.007304271441700154, -0.007304271441700154]], [[-0.028079025579569913, -0.048350137589506736]]]
epoch over
tempforwardpass 

[0.7791898621554525]
cost is
0.08388314352074433
numiter is
221
numwholedata pass is
55
ioindex is 0
simulated deljtheata
[[[-0.009204986336415286, 0.0, -0.009204986336415286]], [[-0.02652852341774118, -0.04278124977561081]]]
real deljtheta
deljtheta is
[[[-0.009204986336415286, -0.0, -0.009204986336415286]], [[-0.02652852341774118, -0.04278124977561081]]]
epoch over
tempforwardpass is
[0.7681984179594065]
tempforwardpass is
[0.768706416103571]
tempforwardpass is
[0.7410052799499791]
tempforwardpass is
[0.7903352996667442]
cost is
0.08405018799291901
numiter is
222
numwholedata pass is
55
ioindex is 1
simulated deljtheata
[[[-0.005697678693868883, -0.005697678693868883, -0.005697678693868883]], [[-0.025092251298293206, -0.03308552178347044]]]
real deljtheta
deljtheta is
[[[-0.005697678693868883, -0.005697678693868883, -0.005697678693868883]], [[-0.025092251298293206, -0.03308552178347044]]]
epoch over
tempforwardpass is
[0.7772006965036046]
tempforwardpass is
[0.7777064194821672]
tempf

[[[-0.01374735314158362, 0.0, -0.01374735314158362]], [[-0.030251139539713753, -0.04694740613129385]]]
real deljtheta
deljtheta is
[[[-0.01374735314158362, -0.0, -0.01374735314158362]], [[-0.030251139539713753, -0.04694740613129385]]]
epoch over
tempforwardpass is
[0.7571843717390608]
tempforwardpass is
[0.7576679541080501]
tempforwardpass is
[0.6972029725612037]
tempforwardpass is
[0.7976750865842297]
cost is
0.0771772617660266
numiter is
293
numwholedata pass is
73
ioindex is 0
simulated deljtheata
[[[0.0, -0.012761034889299541, -0.012761034889299541]], [[-0.027764155563504127, -0.04280459646429757]]]
real deljtheta
deljtheta is
[[[-0.0, -0.012761034889299541, -0.012761034889299541]], [[-0.027764155563504127, -0.04280459646429757]]]
epoch over
tempforwardpass is
[0.7695652361779843]
tempforwardpass is
[0.769354990483228]
tempforwardpass is
[0.7094135448975473]
tempforwardpass is
[0.8088313144083685]
cost is
0.07740963809388463
numiter is
294
numwholedata pass is
73
ioindex is 1
simul

...

numiter is
8314
numwholedata pass is
2078
ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.0004395700338475649]], [[5.5768436058777396e-05, 0.0007790095612890716]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0004395700338475649]], [[5.5768436058777396e-05, 0.0007790095612890716]]]
epoch over
tempforwardpass is
[0.9778275272495967]
tempforwardpass is
[0.9778260944911046]
tempforwardpass is
[0.03379838035587942]
tempforwardpass is
[0.9892631860777995]
cost is
0.0001079098588147352
numiter is
8315
numwholedata pass is
2078
ioindex is 2
simulated deljtheata
[[[-0.00017893001951607248, 0.0, -0.00017893001951607248]], [[-0.00024086035986183667, -0.00026395733917896247]]]
real deljtheta
deljtheta is
[[[-0.00017893001951607248, -0.0, -0.00017893001951607248]], [[-0.00024086035986183667, -0.00026395733917896247]]]
epoch over
tempforwardpass is
[0.9778406408198477]
tempforwardpass is
[0.9778418367638538]
tempforwardpass is
[0.03381086142255963]
tempforwardpass is
[0.9892685677035314]
cost is
0.0

ioindex is 0
simulated deljtheata
[[[0.0, -0.0001756849054091624, -0.0001756849054091624]], [[-0.00023681052705442227, -0.0002594554257755464]]]
real deljtheta
deljtheta is
[[[-0.0, -0.0001756849054091624, -0.0001756849054091624]], [[-0.00023681052705442227, -0.0002594554257755464]]]
epoch over
tempforwardpass is
[0.9779771146808729]
tempforwardpass is
[0.9779731650295634]
tempforwardpass is
[0.033640955815494394]
tempforwardpass is
[0.989324706919345]
cost is
0.000106068167927242
numiter is
8410
numwholedata pass is
2102
ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.00043353536723719836]], [[5.492755386440949e-05, 0.0007685495515260372]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.00043353536723719836]], [[5.492755386440949e-05, 0.0007685495515260372]]]
epoch over
tempforwardpass is
[0.9779531471292502]
tempforwardpass is
[0.9779491918867077]
tempforwardpass is
[0.033607910127690876]
tempforwardpass is
[0.9893159794370383]
cost is
0.00010601874312507099
numiter is
8411
numwholedata

[[[-3.964027863675378e-08, -3.964027863675378e-08, -3.964027863675378e-08]], [[-6.66602811129162e-06, -6.670689291534187e-06]]]
epoch over
tempforwardpass is
[0.9780698739490183]
tempforwardpass is
[0.9780684989858687]
tempforwardpass is
[0.03342979989736596]
tempforwardpass is
[0.9893661019246613]
cost is
0.00010425574675538196
numiter is
8505
numwholedata pass is
2126
ioindex is 0
simulated deljtheata
[[[0.0, -0.0001731573069240038, -0.0001731573069240038]], [[-0.00023360352194430378, -0.00025589160746703447]]]
real deljtheta
deljtheta is
[[[-0.0, -0.0001731573069240038, -0.0001731573069240038]], [[-0.00023360352194430378, -0.00025589160746703447]]]
epoch over
tempforwardpass is
[0.9780849576598738]
tempforwardpass is
[0.9780810723897551]
tempforwardpass is
[0.03344176323974504]
tempforwardpass is
[0.9893712705019326]
cost is
0.0001042425792394076
numiter is
8506
numwholedata pass is
2126
ioindex is 1
simulated deljtheata
[[[-3.9276473709548034e-08, -3.9276473709548034e-08, -3.927647

tempforwardpass is
[0.9781739318564735]
tempforwardpass is
[0.03323405164477711]
tempforwardpass is
[0.989411590725582]
cost is
0.00010248082460181808
numiter is
8600
numwholedata pass is
2149
ioindex is 3
simulated deljtheata
[[[-3.6442932904136615e-08, -3.6442932904136615e-08, -3.6442932904136615e-08]], [[-6.160068900914467e-06, -6.1643490591942185e-06]]]
real deljtheta
deljtheta is
[[[-3.6442932904136615e-08, -3.6442932904136615e-08, -3.6442932904136615e-08]], [[-6.160068900914467e-06, -6.1643490591942185e-06]]]
epoch over
tempforwardpass is
[0.9781755612807819]
tempforwardpass is
[0.9781741845970713]
tempforwardpass is
[0.03323426445513583]
tempforwardpass is
[0.9894117198010024]
cost is
0.00010248054741655143
numiter is
8601
numwholedata pass is
2150
ioindex is 0
simulated deljtheata
[[[-0.00017074748956754987, 0.0, -0.00017074748956754987]], [[-0.00023052661390151455, -0.0002524746450151416]]]
real deljtheta
deljtheta is
[[[-0.00017074748956754987, -0.0, -0.00017074748956754987]]

[0.9894512677682125]
cost is
0.00010076710148265891
numiter is
8695
numwholedata pass is
2173
ioindex is 2
simulated deljtheata
[[[0.0, -0.00016868512076594788, -0.00016868512076594788]], [[-0.00022788729049769038, -0.00024954208113444926]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00016868512076594788, -0.00016868512076594788]], [[-0.00022788729049769038, -0.00024954208113444926]]]
epoch over
tempforwardpass is
[0.9782787874612345]
tempforwardpass is
[0.9782774416632104]
tempforwardpass is
[0.033042015809495326]
tempforwardpass is
[0.9894562688168594]
cost is
0.00010075441668786246
numiter is
8696
numwholedata pass is
2173
ioindex is 3
simulated deljtheata
[[[-3.3365157904048616e-08, -3.3365157904048616e-08, -3.3365157904048616e-08]], [[-5.668594563264626e-06, -5.672508689976329e-06]]]
real deljtheta
deljtheta is
[[[-3.3365157904048616e-08, -3.3365157904048616e-08, -3.3365157904048616e-08]], [[-5.668594563264626e-06, -5.672508689976329e-06]]]
epoch over
tempforwardpass is
[0.9782790189

In [ ]:
pow(10,-3)